# Random Forest - Tania

In [ ]:
#install libraries
!pip install scikeras
!pip install np_utils

#import dependencies and other ML libraries
import tensorflow as tf
from keras.utils import to_categorical
from scikeras.wrappers import KerasClassifier
from sklearn.metrics import classification_report, confusion_matrix, accuracy_score, f1_score, roc_curve, auc
from sklearn.model_selection import train_test_split, RandomizedSearchCV, learning_curve, cross_val_score
from sklearn.preprocessing import LabelEncoder
from sklearn.svm import SVC
from sklearn.linear_model import LogisticRegression
from sklearn.tree import DecisionTreeClassifier
from sklearn.neighbors import KNeighborsClassifier
from sklearn.discriminant_analysis import LinearDiscriminantAnalysis

# Commonly used supporting libraries
from matplotlib import pyplot as plt
import numpy as np
import pandas as pd
from pandas.plotting import scatter_matrix
import seaborn as sns

from sklearn.ensemble import RandomForestClassifier


In [ ]:
#Load Waterfowl Dataset

csv="WaterfowlData.csv"

#Read data
#dataset=pd.read_csv(csv)
dataset = pd.read_csv(csv, on_bad_lines='skip', engine='python')
dataset.head()

NameError: name 'pd' is not defined

In [ ]:
#Cleaning up rows and columns
dataset.shape

#Showing descriptive statistics
dataset.describe()

event-id visible                timestamp       location-long  \
count        870144  870139                   870138              870137   
unique       464815      17                   451895              196961   
top     37505122235    true  2024-12-03 19:11:44.000  -89.48255920410156   
freq              2  870122                        8                  98   

              location-lat acceleration-raw-x acceleration-raw-y  \
count               870135             870132             870128   
unique              245269               2227               2245   
top     36.115718841552734                0.0                0.0   
freq                   107               4658               4061   

       acceleration-raw-z bar:barometric-height battery-charge-percent  ...  \
count              870123                870121                 870118  ...   
unique               2784                    32                    131  ...   
top                 987.0                   0.0                    100  ...   
freq                 7408                870083                 481128  ...   

       mag:magnetic-field-raw-x mag:magnetic-field-raw-y  \
count                    870082                   870078   
unique                     8909                     8870   
top                         0.0                      0.0   
freq                       3636                     3288   

       mag:magnetic-field-raw-z orn:transmission-protocol tag-voltage  \
count                    870075                    870073      870068   
unique                     6388                        19         539   
top                         0.0                      GPRS      4168.0   
freq                       3305                    867277       19524   

       sensor-type individual-taxon-canonical-name tag-local-identifier  \
count       870061                          870057               870050   
unique          11                              13                  332   
top            gps              Anas platyrhynchos               234447   
freq        870044                          729694                 7410   

       individual-local-identifier            study-name  
count                       870048                870042  
unique                         331                     3  
top                  WLR-129-M-YR2  Mallard Connectivity  
freq                          7410                870040  

[4 rows x 30 columns]

In [ ]:
#Identifying data types and names of each column
dataset.dtypes

event-id                           object
visible                            object
timestamp                          object
location-long                      object
location-lat                       object
acceleration-raw-x                 object
acceleration-raw-y                 object
acceleration-raw-z                 object
bar:barometric-height              object
battery-charge-percent             object
battery-charging-current           object
external-temperature               object
gps:hdop                           object
gps:satellite-count                object
gps-time-to-fix                    object
ground-speed                       object
heading                            object
height-above-msl                   object
import-marked-outlier              object
gls:light-level                    object
mag:magnetic-field-raw-x           object
mag:magnetic-field-raw-y           object
mag:magnetic-field-raw-z           object
orn:transmission-protocol          object
tag-voltage                        object
sensor-type                        object
individual-taxon-canonical-name    object
tag-local-identifier               object
individual-local-identifier        object
study-name                         object
dtype: object

In [ ]:
#Checking for any null values
dataset.isnull().sum()

event-id                             0
visible                              5
timestamp                            6
location-long                        7
location-lat                         9
acceleration-raw-x                  12
acceleration-raw-y                  16
acceleration-raw-z                  21
bar:barometric-height               23
battery-charge-percent              26
battery-charging-current            27
external-temperature                32
gps:hdop                            36
gps:satellite-count                 39
gps-time-to-fix                     42
ground-speed                        47
heading                             48
height-above-msl                    50
import-marked-outlier               52
gls:light-level                     57
mag:magnetic-field-raw-x            62
mag:magnetic-field-raw-y            66
mag:magnetic-field-raw-z            69
orn:transmission-protocol           71
tag-voltage                         76
sensor-type                         83
individual-taxon-canonical-name     87
tag-local-identifier                94
individual-local-identifier         96
study-name                         102
dtype: int64

In [ ]:
#Checking out data distribution
for x in dataset.columns:
  print(f"Column: {x}")
  print("-"*20)
  print(dataset[x].value_counts())
  print("")

Column: event-id
--------------------
event-id
37505122235    2
37505122234    2
37505122233    2
37505122194    2
37505122195    2
              ..
37250744431    1
37570059790    1
3761003y"      1
363924554ue    1
36937675775    1
Name: count, Length: 464815, dtype: int64

Column: visible
--------------------
visible
true                       870122
2025-01-12 08:58:12.000         2
50.243247985839844              1
-0.253                          1
-0.606                          1
Mallard Connectivity            1
52.6251106262207                1
24.0                            1
0.361                           1
0.603                           1
159.0                           1
3966.0                          1
236799                          1
tr00                            1
366.0                           1
trhos"                          1
GPRS                            1
Name: count, dtype: int64

Column: timestamp
--------------------
timestamp
2024-12-03 19:11:44.000 

In [ ]:
# Drop irrelevant columns and verify, only if they exist
columns_to_drop = ["battery-charge-percent", "battery-charging-current", "gps-time-to-fix",
                   "orn:transmission-protocol", "tag-voltage", "sensor-type", "visible", "tag-local-identifier"]

for column in columns_to_drop:
    if column in dataset.columns:  # Check if column exists before dropping
        dataset = dataset.drop(columns=[column])
    # else:
    #     print(f"Column '{column}' not found in the DataFrame.") Print a message if the column is not found

dataset.columns #verification

Index(['event-id', 'timestamp', 'location-long', 'location-lat',
       'acceleration-raw-x', 'acceleration-raw-y', 'acceleration-raw-z',
       'bar:barometric-height', 'external-temperature', 'gps:hdop',
       'gps:satellite-count', 'ground-speed', 'heading', 'height-above-msl',
       'import-marked-outlier', 'gls:light-level', 'mag:magnetic-field-raw-x',
       'mag:magnetic-field-raw-y', 'mag:magnetic-field-raw-z',
       'individual-taxon-canonical-name', 'individual-local-identifier',
       'study-name'],
      dtype='object')

In [ ]:
# Convert to numeric values
for x in dataset.columns:
  dataset[x], _ = pd.factorize(dataset[x])

#check data
dataset.head()

event-id  timestamp  location-long  location-lat  acceleration-raw-x  \
0         0          0              0             0                   0   
1         1          1              1             1                   1   
2         2          2              2             2                   2   
3         3          3              3             3                   3   
4         4          4              4             4                   4   

   acceleration-raw-y  acceleration-raw-z  bar:barometric-height  \
0                   0                   0                      0   
1                   1                   1                      0   
2                   2                   2                      0   
3                   3                   3                      0   
4                   4                   4                      0   

   external-temperature  gps:hdop  ...  heading  height-above-msl  \
0                     0         0  ...        0                 0   
1                     1         1  ...        1                 1   
2                     2         2  ...        2                 2   
3                     2         3  ...        3                 3   
4                     3         3  ...        4                 4   

   import-marked-outlier  gls:light-level  mag:magnetic-field-raw-x  \
0                      0                0                         0   
1                      0                1                         1   
2                      0                1                         2   
3                      0                1                         3   
4                      0                1                         4   

   mag:magnetic-field-raw-y  mag:magnetic-field-raw-z  \
0                         0                         0   
1                         1                         1   
2                         2                         2   
3                         3                         3   
4                         4                         4   

   individual-taxon-canonical-name  individual-local-identifier  study-name  
0                                0                            0           0  
1                                0                            0           0  
2                                0                            0           0  
3                                0                            0           0  
4                                0                            0           0  

[5 rows x 22 columns]

In [ ]:
#Algorithm to start splitting between training and test sets

# Labels
y = dataset['event-id']
# Features
X = dataset.drop(columns = 'event-id')

#Split data into training and test sets
X_train, X_test, y_train, y_test = train_test_split(X, y, random_state=1)

#Split training data into training and validation
X_train, X_validate, y_train, y_validate = train_test_split(X_train, y_train, random_state=1)

In [ ]:
# Convert to numpy arrays
X_train = X_train.to_numpy()
X_validate = X_validate.to_numpy()
X_test = X_test.to_numpy()

y_train = y_train.to_numpy()
y_validate = y_validate.to_numpy()
y_test = y_test.to_numpy()

In [ ]:
#Checking shape of the new datasets

print(f"Shape of X_train: {X_train.shape}")
print(f"Shape of X_test: {X_test.shape}")
print(f"Shape of X_validate: {X_validate.shape}")

print(f"Shape of y_train: {y_train.shape}")
print(f"Shape of y_test: {y_test.shape}")
print(f"Shape of y_validate: {y_validate.shape}")

Shape of X_train: (489456, 21)
Shape of X_test: (217536, 21)
Shape of X_validate: (163152, 21)
Shape of y_train: (489456,)
Shape of y_test: (217536,)
Shape of y_validate: (163152,)


In [ ]:
train_class_counts = {label: (y_train == label).sum() for label in np.unique(y_train)}
test_class_counts = {label: (y_test == label).sum() for label in np.unique(y_test)}

print(f"Distribution of y_train: {train_class_counts}")
print(f"Distribution of y_test: {test_class_counts}")

Distribution of y_train: {1: 1, 2: 1, 3: 1, 6: 1, 7: 1, 11: 1, 12: 1, 15: 1, 21: 1, 23: 1, 25: 1, 26: 1, 28: 1, 29: 1, 30: 1, 34: 1, 37: 1, 38: 1, 39: 1, 40: 1, 41: 1, 44: 1, 46: 1, 48: 1, 49: 1, 50: 1, 52: 1, 54: 1, 55: 1, 57: 1, 58: 1, 59: 1, 60: 1, 62: 1, 63: 1, 65: 1, 66: 1, 69: 1, 70: 1, 71: 1, 73: 1, 74: 1, 76: 1, 77: 1, 78: 1, 79: 1, 82: 1, 83: 1, 84: 1, 85: 1, 86: 1, 89: 1, 90: 1, 91: 1, 93: 1, 95: 1, 97: 1, 98: 1, 99: 1, 101: 1, 104: 1, 105: 1, 106: 1, 107: 1, 108: 1, 112: 1, 113: 1, 115: 1, 116: 1, 117: 1, 119: 1, 123: 1, 126: 1, 131: 1, 132: 1, 133: 1, 134: 1, 135: 1, 139: 1, 140: 1, 141: 1, 143: 1, 145: 1, 147: 1, 149: 1, 150: 1, 153: 1, 155: 1, 156: 1, 157: 1, 158: 1, 161: 1, 162: 1, 163: 1, 164: 1, 166: 1, 169: 1, 170: 1, 173: 1, 174: 1, 175: 1, 177: 1, 178: 1, 179: 1, 180: 1, 182: 1, 183: 1, 184: 1, 185: 1, 189: 1, 192: 1, 194: 1, 200: 1, 201: 1, 206: 1, 207: 1, 210: 1, 211: 1, 212: 1, 213: 1, 216: 1, 217: 1, 218: 1, 219: 1, 220: 1, 221: 1, 223: 1, 225: 1, 227: 1, 230: 1

In [ ]:
#Creating learning curve (NOTE TO SELF: NEED TO PICKUP FROM HERE)

def plotLearningCurve(model, title, X, y, ax=None):
  train_sizes, train_scores, test_scores = learning_curve(model, X, y, cv=5, n_jobs=-1, train_sizes=np.linspace(0.1, 1.0, 5))
  train_scores_mean = np.mean(train_scores, axis=1)
  train_scores_std = np.std(train_scores, axis=1)
  test_scores_mean = np.mean(test_scores, axis=1)
  test_scores_std = np.std(test_scores, axis=1)
  if ax is None:
    plt.figure()
    ax = plt.gca()
  ax.set_title(title)
  ax.set_xlabel("Training examples")
  ax.set_ylabel("Score")
  ax.grid()
  ax.fill_between(train_sizes, train_scores_mean - train_scores_std,
                  train_scores_mean + train_scores_std, alpha=0.1, color="r")
  ax.fill_between(train_sizes, test_scores_mean - test_scores_std,
                  test_scores_mean + test_scores_std, alpha=0.1, color="purple")
  ax.plot(train_sizes, train_scores_mean, 'o-', color='r',
          label="Training score")
  ax.plot(train_sizes, test_scores_mean, 'o-', color='purple',
          label="Cross-validation score")
  ax.legend(loc="best")
  return ax

In [ ]:
#Creating ROC Curve

def plot_roc_curve(model, X, y, ax=None):
  if hasattr(model, "decision_function"):
    scores = model.decision_function(X)
  else:
    scores=model.predict(X)
  fpr, tpr, _ = roc_curve(y, scores)
  roc_auc = auc(fpr, tpr)
  if ax is None:
    plt.figure()
    ax = plt.gca()
  ax.plot(fpr, tpr, label='ROC curve (area = %0.2f)' % roc_auc, color='hotpink')
  ax.plot([0,1],[0,1], 'k--')
  ax.set_xlim([0.0,1.0])
  ax.set_ylim([0.0,1.05])
  ax.set_xlabel('False Positive Rate')
  ax.set_ylabel('True Positive Rate')
  ax.set_title('ROC Curve')
  ax.legend(loc="lower right")
  return ax

In [ ]:
# Loop over each model in an array of models.
def evaluate_model(model, X_train, y_train, X_test, y_test, name):
    # Fit the model
    model.fit(X_train, y_train)
    # Make predictions
    y_pred = model.predict(X_test)
    # Evaluate Accuracy
    accuracy = accuracy_score(y_test, y_pred)
    # Evaluate F1
    f1 = f1_score(y_test, y_pred)

    ## Print Results
    print(f"Model: {name}, Accuracy: {accuracy}, F1 Score: {f1}")

    # Plot the Learning Curve and ROC Curve
    fig, axes = plt.subplots(1,3, figsize=(12,6))
    fig.suptitle(f"{name} - Accuracy: {accuracy}, F1 Score: {f1}")
    plotLearningCurve(model, f"Learning Curve - {name}", X_train, y_train, ax=axes[0])
    plot_roc_curve(model, X_test, y_test, ax=axes[1])

    # Plot Confusion Matrix
    cm = confusion_matrix(y_test, y_pred)
    sns.heatmap(cm, annot=True, fmt='d', cmap='Blues', ax=axes[2])
    axes[2].set_title("Confusion Matrix")
    axes[2].set_xlabel(" Predicted Labels")
    axes[2].set_ylabel("True Labels")

    #plt.savefig(f"learning_curve-ROC-images/{name}training.png")
    plt.show()
    print("\n")

    # Print Classification Report
    print("Classification Report: ")
    print(classification_report(y_test, y_pred))

In [ ]:
# Initializes an array called models.
models = []
models.append(('FOREST', RandomForestClassifier()))

In [ ]:
for name, model in models:
  evaluate_model(model, X_train, y_train, X_test, y_test, name)

In [ ]:
#Hypertuning based on results^^^^




# Random Forest Classifier
#param_rf = {

#best_model_rf_random = model_hypertuning(RandomForestClassifier(), param_rf, X_validate, y_validate, n_iter=10)
#print(f"Best parameters for Random Forest Classifier (Randomized): {best_model_rf_random}")
# Initializes an array called models.
#models = []
#models.append(('FOREST', RandomForestClassifier(n_estimators=200, min_samples_split=5, min_samples_leaf=1, max_depth=30)))

In [ ]:
#for name, model in models:
 # evaluate_model(model, X_train, y_train, X_test, y_test, name)